# Projet de base en local

In [1]:
import os
import sys
KAGGLE_AGENT_PATH = "/kaggle_simulations/agent/"
if os.path.exists(KAGGLE_AGENT_PATH):
    sys.path.insert(0, os.path.join(KAGGLE_AGENT_PATH, 'lib'))
else:
    sys.path.insert(0, os.path.join(os.getcwd(), 'lib'))
    

Pour essayer tout de suite si tout fonctionne

In [3]:
# Train a PPO agent
from environment import KoreGymEnv
from stable_baselines3 import PPO

kore_env = KoreGymEnv(agents=[None, 'test.py'])
model = PPO('MlpPolicy', kore_env, verbose=1)
model.learn(total_timesteps=100000) 

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 768      |
|    ep_rew_mean     | 1.78e+04 |
| time/              |          |
|    fps             | 40       |
|    iterations      | 1        |
|    time_elapsed    | 50       |
|    total_timesteps | 2048     |
---------------------------------


KeyboardInterrupt: 

### Pour vérifier que l'environement est valide

In [6]:
# The bad news: this check will fail in the kaggle docker environment. The most likely reason is a version mismatch between packages.
# The good news: That's alright since everything else works! We're doing some unconventional dependency management here, so we'll have to live with
# a failed check.

from stable_baselines3.common.env_checker import check_env
from environment import KoreGymEnv

env = KoreGymEnv()
check_env(env)

C:\Users\Jayma\AppData\Roaming\Python\Python39\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
c:\Users\Jayma\Documents\Python\Openclassroms\Projet_8_Kore\lib\stable_baselines3\common\env_checker.py:278: UserWarning: Your action space has dtype float64, we recommend using np.float32 to avoid cast errors.
  warnings.warn(


AttributeError: module 'gym' has no attribute 'GoalEnv'

## Visualiser une partie

In [1]:
from kaggle_environments import make
env = make("kore_fleets", debug=True)
from kaggle_environments.envs.kore_fleets.starter_bots.python.main import agent

In [2]:
# "opponent/main.py" --> le principal enemie
# "opponent.py" --> une copie du modèle
# "test.py" --> pour faire des tests
# "main.py" --> le modèle actuel
env.run(["test.py", "opponent/main.py"])
env.render(mode="ipython", width=1000, height=800)

## Entrainer l'agent

In [1]:
import os
import sys
KAGGLE_AGENT_PATH = "/kaggle_simulations/agent/"
if os.path.exists(KAGGLE_AGENT_PATH):
    sys.path.insert(0, os.path.join(KAGGLE_AGENT_PATH, 'lib'))
else:
    sys.path.insert(0, os.path.join(os.getcwd(), 'lib'))
    
from stable_baselines3 import PPO
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.monitor import Monitor
from environment import KoreGymEnv

    

In [8]:
kore_env = KoreGymEnv(agents=[None, "opponent/main.py"])  # TODO: This seed is not enough. Seed everything! config=dict(randomSeed=997269658)
monitored_env = Monitor(env=kore_env)
model = PPO('MlpPolicy', monitored_env, verbose=1)

Using cpu device
Wrapping the env in a DummyVecEnv.


changer d'adversaire

In [2]:
model = PPO.load('opponent_agent')
kore_env = KoreGymEnv(agents=[None, "opponent/main.py"])  # TODO: This seed is not enough. Seed everything! config=dict(randomSeed=997269658)
monitored_env = Monitor(env=kore_env)
model.set_env(monitored_env)

Wrapping the env in a DummyVecEnv.


Phase d'apprentissage

In [3]:
%%time
# For serious training, likely many more iterations will be needed, as well as hyperparameter tuning!
# Even so, sometimes training will still fail. RL is like that. Try a couple times with the same config before giving up!
model.learn(total_timesteps=100000)  

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 506      |
|    ep_rew_mean     | 450      |
| time/              |          |
|    fps             | 17       |
|    iterations      | 1        |
|    time_elapsed    | 117      |
|    total_timesteps | 2048     |
---------------------------------
-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 498           |
|    ep_rew_mean          | 169           |
| time/                   |               |
|    fps                  | 18            |
|    iterations           | 2             |
|    time_elapsed         | 221           |
|    total_timesteps      | 4096          |
| train/                  |               |
|    approx_kl            | 0.00063537864 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -7.29         |
|    explained_variance   | 0.348         |


Regarder une partie à la volé

In [6]:
# Watch it mercilessly beat the baseline bot - Note: The current episode might not be over yet
kore_env.render(mode="ipython", width=1000, height=800)

Sauvegarder le modèle actuel

In [25]:
# model.save("main_agent")
model.save("opponent_agent")

## Evaluer les performances

In [11]:
import numpy as np

eval_env = KoreGymEnv(config=dict(strict=True))  # The 'strict' flags sets rewards to 1 if the agent won the episode and 0 else. Useful for evaluation.
monitored_env = Monitor(env=eval_env)
model_loaded = PPO.load('baseline_agent')

def evaluate(model, num_episodes=1):
    """
    Evaluate a RL agent - Adapted from 
    https://colab.research.google.com/github/Stable-Baselines-Team/rl-colab-notebooks/blob/sb3/stable_baselines_getting_started.ipynb
    :param model: (BaseRLModel object) the RL Agent
    :param num_episodes: (int) number of episodes to evaluate it
    :return: (float) Mean reward for the last num_episodes
    """
    all_episode_rewards = []
    for i in range(num_episodes):
        episode_rewards = []
        done = False
        obs = monitored_env.reset()
        while not done:
            action, _ = model.predict(obs)
            obs, _, done, info = monitored_env.step(action)
            if done:
                agent_reward = monitored_env.env.raw_obs.players[0][0]
                opponent_reward = monitored_env.env.raw_obs.players[1][0]
                reward = agent_reward > opponent_reward
                print(reward)
            else:
                reward = 0
            # monitored_env.render(mode='ipython', height=400, width=300)
            episode_rewards.append(reward)

        all_episode_rewards.append(sum(episode_rewards))

    mean_episode_reward = np.mean(all_episode_rewards)
    print("Mean reward:", mean_episode_reward, "Num episodes:", num_episodes)

    return mean_episode_reward

evaluate(model_loaded, 3)

True
False
False
Mean reward: 0.3333333333333333 Num episodes: 3


0.3333333333333333

### Préparer la soumission

In [15]:
%%capture
# This is for debugging purposes only before submitting - Are there any errors?
from kaggle_environments import make
from config import OPPONENT
env = make("kore_fleets", debug=True)
env.run(['main.py', OPPONENT])

In [16]:
!tar -czf submission.tar.gz main.py config.py environment.py reward_utils.py baseline_agent.zip lib